In [1]:
import torch
import numpy as np
import glob
import os
from os.path import join as opj
from torch.utils.data import Dataset
import matplotlib.pyplot as plt
import tqdm
from dataset import TimeSeriesDataset
from models import MaskedAutoencoder, MaskedAutoencoderLightning
from utils import get_model_output,evaluate_reconstructions
from sklearn.model_selection import train_test_split
import wandb
from pytorch_lightning.loggers import WandbLogger
import pytorch_lightning as pl
from pytorch_lightning.callbacks import EarlyStopping, ModelCheckpoint


random_seed = 42

/home/matteo/anaconda3/envs/borg/lib/python3.8/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# 0. Data Loading

In [2]:
# define the data path
data_path = "/srv/nfs-data/janeway/UDGSL_Dataset/HCP"
target_path =  "/srv/nfs-data/janeway/fMRI_foundation_model_ICA"

# choose the ica dimensionality
d_in = 25
ica = f"ica{d_in}"

#get the list of subjects
file_list = glob.glob(opj(data_path,ica,"*.npy"))

# split the data into training and testing
train_list, test_list = train_test_split(file_list, test_size=0.2, random_state=random_seed)

In [3]:
# create the datasets

train_dataset = TimeSeriesDataset(train_list)
test_dataset = TimeSeriesDataset(test_list)



In [4]:
N_EPOCHS = 5000
WARMUP_EPOCHS = 500 

In [5]:
sweep_config = {
    'method': 'random',  # Random search method
    'metric': {
        'name': 'val_loss',
        'goal': 'minimize'  # We want to minimize the training loss
    },
    'parameters': {
        'patch_size': {
            'values': [20, 40, 60]
        },
        'batch_size': {'values': [32, 64, 128]},

        'd_model': {
            'values': [64, 128, 512]
        },
        'learning_rate': {'values' : [1e-3, 1e-4, 1e-5]},
        'weight_decay': {'values' : [0, 1e-2,1e-3, 1e-4, 1e-5]},
        'mask_ratio': {'values' : [0.25, 0.5, 0.75, 0.9]},
        
        'num_encoder_layers': {
            'values': [4, 6, 8]
        },
        'nhead': {
            'values': [4, 8, 16]
        },
        'dim_feedforward': {
            'values': [128, 256, 512]
        },
        'dropout': {'values':[0, 0.1]},
        'masked_loss': {'values':[True, False]},
    }
}


In [6]:
def train(config=None):
    # Initialize a new W&B run
    with wandb.init(config=config):
        config = wandb.config


        batch_size = config.batch_size
        train_loader = torch.utils.data.DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
        test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=batch_size, shuffle=False)

        ## compute steps
        steps_per_epoch = len(train_loader.dataset) // batch_size 
        total_steps = steps_per_epoch * N_EPOCHS
        warmup_steps = steps_per_epoch * WARMUP_EPOCHS

        #Define folder for saving the model checkpoints
        checkpoint_dir = os.path.join(target_path, wandb.run.name)
        os.makedirs(checkpoint_dir, exist_ok=True)

        # Callbacks for early stopping and checkpointing
        early_stopping = EarlyStopping(
            monitor='val_loss',
            patience=3,  # Stop after 3 epochs without improvement
            verbose=True,
            mode='min'
        )

        checkpoint_callback = ModelCheckpoint(
            dirpath=checkpoint_dir,  # Save in the unique run folder
            filename='{epoch:02d}-{val_loss:.2f}',  # File format
            monitor='val_loss',  # Monitor validation loss
            save_top_k=1,  # Save only the best model
            mode='min',  # Minimize the val_loss
            verbose=True
        )




        # Initialize your model with the hyperparameters from the sweep config
        model = MaskedAutoencoderLightning(
            patch_size=config.patch_size,  # You can modify this as per your use case
            d_in=d_in,
            d_model=config.d_model,
            nhead=config.nhead,
            num_encoder_layers=config.num_encoder_layers,
            num_decoder_layers=config.num_encoder_layers//2, #to make the decoder shallower
            dim_feedforward=config.dim_feedforward,
            dropout=config.dropout,
            learning_rate=config.learning_rate,
            weight_decay=config.weight_decay,
            masked_loss=config.masked_loss,  # Adjust this if necessary
            mask_ratio=config.mask_ratio,
            warmup_steps=warmup_steps,
            max_steps=total_steps  # You can calculate or adjust this based on your dataset
        )

        # Initialize PyTorch Lightning trainer with WandB logger
        wandb_logger = WandbLogger()  # Use WandB as logger
        trainer = pl.Trainer(
            logger=wandb_logger,
            max_epochs=N_EPOCHS,  # Adjust the number of epochs as needed
            devices = [3],
            log_every_n_steps=steps_per_epoch, ## Log every epoch,
            callbacks=[early_stopping, checkpoint_callback],  # Add callbacks

            )
        
        
        

        # Assuming you have your dataloader defined (train_loader)
        trainer.fit(model, train_loader, test_loader)
        
        print("Running evaluation")
        reconstructions, ground_truths, masks, latents, labels = get_model_output(model,test_loader)
        
        avg_r2, avg_pearson, avg_mse = evaluate_reconstructions(ground_truths,reconstructions)
        
        wandb.log({"R2" : avg_r2, "Pearson Correlation" : avg_pearson, "MSE" : avg_mse})
        print({"R2" : avg_r2, "Pearson Correlation" : avg_pearson, "MSE" : avg_mse})

        


In [ ]:
# Initialize the sweep
sweep_id = wandb.sweep(sweep_config, project='ICA foundation model')

# Run the sweep with the train function
wandb.agent(sweep_id, function=train, count=20)  # count specifies how many different configurations to try


Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.


Create sweep with ID: e9o2yxfu
Sweep URL: https://wandb.ai/matteoferrante/ICA%20foundation%20model/sweeps/e9o2yxfu


wandb: Agent Starting Run: n7ewinv0 with config:
wandb: 	batch_size: 32
wandb: 	d_model: 128
wandb: 	dim_feedforward: 128
wandb: 	dropout: 0.1
wandb: 	learning_rate: 0.0001
wandb: 	mask_ratio: 0.25
wandb: 	masked_loss: True
wandb: 	nhead: 8
wandb: 	num_encoder_layers: 8
wandb: 	patch_size: 60
wandb: 	weight_decay: 0.001
Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: matteoferrante. Use `wandb login --relogin` to force relogin


/home/matteo/anaconda3/envs/borg/lib/python3.8/site-packages/torch/nn/modules/transformer.py:286: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)
  warnings.warn(f"enable_nested_tensor is True, but self.use_nested_tensor is False because {why_not_sparsity_fast_path}")
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
You are using a CUDA device ('NVIDIA H100 PCIe') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_precision('medium' | 'high')` which will trade-off precision for performance. For more details, read https://pytorch.org/docs/stable/generated/torch.set_float32_matmul_precision.html#torch.set_float32_matmul_precision
/home/matteo/anaconda3/envs/borg/lib/python3.8/site-packages/pytorch_lightning/loggers/wandb.py:396: There is a wandb ru

Sanity Checking: |                                                                                                                     | 0/? [00:00<?, ?it/s]

...

Monitored metric val_loss did not improve in the last 3 records. Best score: 0.160. Signaling Trainer to stop.
Epoch 99, global step 2600: 'val_loss' was not in top 1


Epoch 99: 100%|███████████| 26/26 [00:01<00:00, 14.65it/s, v_num=ho8z, learning_rate=0.000208, train_loss_step=0.153, val_loss=0.160, train_loss_epoch=0.165]
Running evaluation


100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 7/7 [00:00<00:00, 13.46it/s]


Average R² Score: 0.3608
Average Pearson Correlation: 0.6024
Average Mean Squared Error (MSE): 0.6154
{'R2': 0.36077024400402186, 'Pearson Correlation': 0.6024308660119871, 'MSE': 0.6154333952054456}


wandb: Agent Starting Run: mv4ai662 with config:
wandb: 	batch_size: 32
wandb: 	d_model: 64
wandb: 	dim_feedforward: 512
wandb: 	dropout: 0
wandb: 	learning_rate: 0.0001
wandb: 	mask_ratio: 0.25
wandb: 	masked_loss: True
wandb: 	nhead: 16
wandb: 	num_encoder_layers: 4
wandb: 	patch_size: 20
wandb: 	weight_decay: 0.0001
Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
